In [1]:
from pathlib import Path
from math import inf
from time import perf_counter
import tracemalloc

In [2]:
INPUT_FILE = Path.cwd().parent / "inputs" / "astar_in.txt"

### Helper Functions

This section defines utility functions that support the main algorithms. These include functions for displaying the puzzle state, checking if the current state matches the goal state, and performing basic operations like finding the position of the blank tile or generating possible moves. These helper functions are essential for implementing the search algorithms and heuristics that follow.

In [3]:
def is_square_grid(grid):
    n = len(grid)
    N = int(n ** 0.5)
    return N * N == n

def parse_astar_in(path: Path):
    """ Parses the input file for A* algorithm and returns the start and goal grids as tuples."""

    with open(path, 'r') as f:
        lines = f.readlines()
    
    start, goal = False, False
    start_space, goal_space = False, False
    start_grid, goal_grid = [], []
    for line in lines:
        if line.strip() == 'start':
            start = True
            continue
        
        if line.strip() == 'goal':
            goal = True
            continue
        
        if start and not goal:
            if any(ch.isspace() for ch in line):
                out = []
                for tok in line.split():
                    if tok == '*':
                        start_space = True
                        out.append(0)
                    else:
                        out.append(int(tok))
                start_grid.extend(out)

        if goal:
            if any(ch.isspace() for ch in line):
                out = []
                for tok in line.split():
                    if tok == '*':
                        goal_space = True
                        out.append(0)
                    else:
                        out.append(int(tok))
                goal_grid.extend(out)
    
    if start == False or goal == False:
        raise ValueError("Error: Input file must contain 'start' and 'goal' sections.")
    
    if not start_space or not goal_space:
        raise ValueError("Error: Start and goal grids must both contain spaces ('*').")
    
    if not is_square_grid(start_grid) or not is_square_grid(goal_grid):
        raise ValueError("Error: Start or goal grids must be N*N elements.")
    
    if len(start_grid) != len(goal_grid):
        raise ValueError("Error: Start and goal grids must have the same number of elements.")

    return tuple(start_grid), tuple(goal_grid)

In [4]:
def print_puzzle(state: tuple, N: int = 3, blank: int = 0):
    """ Prints the puzzle state in a readable format, replacing the blank tile with a space."""
    for r in range(N):
        row = state[r*N:(r+1)*N]
        print(" ".join(" " if x == blank else str(x) for x in row))
    print()

def print_path(path, N: int = 3, blank: int = 0):
    """ Prints the sequence of puzzle states in the path, showing each step clearly. """
    for i, state in enumerate(path):
        print(f"Step {i}:")
        print_puzzle(state, N=N, blank=blank)


In [5]:
def neighbors(state: tuple, N: int):
    """ Generates all valid neighboring states by sliding the blank tile in the four possible directions. """
    blank_tile_index = state.index(0)
    blank_tile_index_r, blank_tile_index_c = divmod(blank_tile_index, N)

    successors = []

    for direction_r, direction_c in [(-1,0),(1,0),(0,-1),(0,1)]:
        new_r, new_c = blank_tile_index_r+direction_r, blank_tile_index_c+direction_c
        if 0 <= new_r < N and 0 <= new_c < N:
            nz = new_r*N + new_c
            lst = list(state)
            lst[blank_tile_index], lst[nz] = lst[nz], lst[blank_tile_index]
            successors.append(tuple(lst))

    return successors

In [6]:
def reconstruct(parent, goal: tuple):
    """ Reconstructs the path from the start state to the goal state using the parent mapping."""
    path = []
    cur = goal
    while cur is not None:
        path.append(cur)
        cur = parent[cur]
    return path[::-1]

In [7]:
def generate_ring_order(N: int):
    ring = []

    # Top row
    for col in range(N):
        ring.append(col)

    # Right column (excluding top corner)
    for row in range(1, N):
        ring.append(row * N + (N - 1))

    # Bottom row (excluding right corner)
    for col in range(N - 2, -1, -1):
        ring.append((N - 1) * N + col)

    # Left column (excluding bottom and top corners)
    for row in range(N - 2, 0, -1):
        ring.append(row * N)

    return ring

In [8]:
def astar_algorithm(start: tuple, goal: tuple, heuristic_fn: callable):
    """ Implements the A* search algorithm to find the optimal path from start to goal state using the provided heuristic function."""

    # Step 1: initialization
    OPEN = []               # list of states ready for expansion
    OPEN_SET = set()        # for O(1) membership checks of OPEN
    CLOSED = set()          # expanded states

    Ns = int(len(start) ** 0.5)
    Ng = int(len(goal) ** 0.5)
    if Ns * Ns != len(start) or Ng * Ng != len(goal) or Ns != Ng:
        raise ValueError("Start and goal states must be same size and form an N×N puzzle.")
    N = Ns

    g = {start: 0}
    parent = {start: None}

    OPEN.append(start)
    OPEN_SET.add(start)
    nodes_generated = 1

    goal_positions = {tile: divmod(i, N) for i, tile in enumerate(goal)}

    # h_cache maps state with heuristic value
    h_cache = {}
    # s_cache maps state with sequence score (applicable only for Nilsson's Sequence Score heuristic)
    s_cache = {}
    def h(state):
        if state not in h_cache:
            h_cache[state], s_cache[state] = heuristic_fn(state, goal, goal_positions, N)
        return h_cache[state]
    
    while True:
        # Step 2: Check if OPEN is empty, if true return failure
        if not OPEN:
            raise Exception("No solution found.")
        
        # Step 3: pick n from OPEN with smallest f(n)=g(n)+h(n)
        # Tie-break in favor of goal only when f ties.
        n = min(OPEN, key=lambda s: (g[s] + h(s), 0 if s == goal else 1))
        
        OPEN.remove(n)
        OPEN_SET.remove(n)
        CLOSED.add(n)

        h_val = h(n)
        f_val = g[n] + h_val
        print(f"Expanding: g={g[n]}  h={h_val}  f={f_val}  P={h_cache.get(n,'N/A') if not heuristic_fn.__name__ == 'h_misplaced' else 'None'}  S={s_cache.get(n, 'N/A')}")

        # Step 4: if n is goal, return solution path by tracing parents       
        if n == goal:
            print("Nodes generated:", nodes_generated)
            return reconstruct(parent, n), N
        
        # Step 5: expand n, generate successors
        succ = neighbors(n, N)
        if not succ:
            continue  # "go immediately to 2"

        for ni in succ:
            nodes_generated += 1
            tentative_g = g[n] + 1  # unit step cost for 8-puzzle

            # Step 6: if ni not on OPEN or CLOSED then, add to OPEN, point back to n
            if ni not in OPEN_SET and ni not in CLOSED:
                g[ni] = tentative_g
                parent[ni] = n
                OPEN.append(ni)
                OPEN_SET.add(ni)

            # Step 7: if ni already on OPEN or CLOSED, keep the shorter path (smaller g => smaller f)
            elif tentative_g < g.get(ni, inf):
                g[ni] = tentative_g
                parent[ni] = n

                # if it was on CLOSED and improved, move back to OPEN
                if ni in CLOSED:
                    CLOSED.remove(ni)
                    OPEN.append(ni)
                    OPEN_SET.add(ni)
                # if it's already in OPEN_SET, nothing else needed (its g/parent got improved)

        # Step 8: loop continues

### Misplaced Tile Heuristic Function

The Misplaced Tile heuristic is a simple admissible heuristic for the 8-puzzle problem. It calculates the number of tiles that are not in their correct goal positions, excluding the blank tile. This heuristic provides a lower bound on the number of moves required to reach the goal, as each misplaced tile must be moved at least once. While not as informative as more sophisticated heuristics, it's computationally efficient and guarantees optimality when used with A* search.

In [9]:
def h_misplaced(state: tuple, goal: tuple, goal_positions: dict = None, N: int = 3):
    count = 0
    for s, g in zip(state, goal):
        if s != 0 and s != g:
            count += 1
    return count, None

In [10]:
start, goal = parse_astar_in(INPUT_FILE)

tracemalloc.start()
t0 = perf_counter()
path, N = astar_algorithm(start, goal, h_misplaced)

elapsed = perf_counter() - t0

current, peak = tracemalloc.get_traced_memory()
tracemalloc.stop()

print_path(path, N=N)
print(f"time={elapsed:.4f}s  current={current/1e6:.2f}MB  peak={peak/1e6:.2f}MB")

Expanding: g=0  h=7  f=7  P=None  S=None
Expanding: g=1  h=7  f=8  P=None  S=None
Expanding: g=1  h=7  f=8  P=None  S=None
Expanding: g=1  h=8  f=9  P=None  S=None
Expanding: g=2  h=7  f=9  P=None  S=None
Expanding: g=2  h=7  f=9  P=None  S=None
Expanding: g=2  h=8  f=10  P=None  S=None
Expanding: g=2  h=8  f=10  P=None  S=None
Expanding: g=2  h=8  f=10  P=None  S=None
Expanding: g=3  h=7  f=10  P=None  S=None
Expanding: g=3  h=7  f=10  P=None  S=None
Expanding: g=3  h=8  f=11  P=None  S=None
Expanding: g=3  h=8  f=11  P=None  S=None
Expanding: g=3  h=8  f=11  P=None  S=None
Expanding: g=3  h=8  f=11  P=None  S=None
Expanding: g=3  h=8  f=11  P=None  S=None
Expanding: g=3  h=8  f=11  P=None  S=None
Expanding: g=3  h=8  f=11  P=None  S=None
Expanding: g=3  h=8  f=11  P=None  S=None
Expanding: g=4  h=7  f=11  P=None  S=None
Expanding: g=4  h=7  f=11  P=None  S=None
Expanding: g=4  h=8  f=12  P=None  S=None
Expanding: g=4  h=8  f=12  P=None  S=None
Expanding: g=4  h=8  f=12  P=None  S=Non

### Manhattan Distance Heuristic Function

The Manhattan Distance heuristic measures the total distance each tile needs to move to reach its goal position, calculated as the sum of horizontal and vertical distances for each tile (ignoring obstacles, hence "Manhattan" distance). This heuristic is admissible because it never overestimates the true cost to the goal, as each tile must move at least that many steps. It's more accurate than the Misplaced Tile heuristic and often leads to faster search times in A* algorithm for sliding puzzle problems.

In [11]:
def h_manhattan(state: tuple, goal: tuple, goal_positions: dict = None, N: int = 3):
    if goal_positions is None:
        goal_positions = {tile: divmod(i, N) for i, tile in enumerate(goal)}
    
    distance = 0
    for i, tile in enumerate(state):
        if tile != 0:
            s_r, s_c = divmod(i, N)
            g_r, g_c = goal_positions[tile]
            distance += abs(s_r - g_r) + abs(s_c - g_c)

    return distance, None


In [12]:
start, goal = parse_astar_in(INPUT_FILE)

tracemalloc.start()
t0 = perf_counter()
path, N = astar_algorithm(start, goal, h_manhattan)

elapsed = perf_counter() - t0

current, peak = tracemalloc.get_traced_memory()
tracemalloc.stop()

print_path(path, N=N)
print(f"time={elapsed:.4f}s  current={current/1e6:.2f}MB  peak={peak/1e6:.2f}MB")

Expanding: g=0  h=21  f=21  P=21  S=None
Expanding: g=1  h=20  f=21  P=20  S=None
Expanding: g=1  h=20  f=21  P=20  S=None
Expanding: g=1  h=22  f=23  P=22  S=None
Expanding: g=2  h=21  f=23  P=21  S=None
Expanding: g=2  h=21  f=23  P=21  S=None
Expanding: g=2  h=21  f=23  P=21  S=None
Expanding: g=2  h=21  f=23  P=21  S=None
Expanding: g=2  h=21  f=23  P=21  S=None
Expanding: g=3  h=20  f=23  P=20  S=None
Expanding: g=3  h=20  f=23  P=20  S=None
Expanding: g=3  h=20  f=23  P=20  S=None
Expanding: g=3  h=20  f=23  P=20  S=None
Expanding: g=3  h=20  f=23  P=20  S=None
Expanding: g=3  h=20  f=23  P=20  S=None
Expanding: g=3  h=20  f=23  P=20  S=None
Expanding: g=3  h=20  f=23  P=20  S=None
Expanding: g=4  h=19  f=23  P=19  S=None
Expanding: g=4  h=19  f=23  P=19  S=None
Expanding: g=4  h=19  f=23  P=19  S=None
Expanding: g=5  h=18  f=23  P=18  S=None
Expanding: g=5  h=18  f=23  P=18  S=None
Expanding: g=5  h=18  f=23  P=18  S=None
Expanding: g=6  h=17  f=23  P=17  S=None
Expanding: g=6  

### Nilsson's Sequence Score

Nilsson's Sequence Score is a more sophisticated heuristic that combines sequence scoring with Manhattan distance. It evaluates the puzzle state by considering both the positions of tiles and their ordering in rows and columns. This heuristic assigns penalties for tiles that are out of sequence and adds the Manhattan distance component. While more computationally expensive than simpler heuristics, it provides a tighter bound and can significantly reduce the search space in A* algorithm for certain puzzle configurations.

In [13]:
def h_nilsson(state: tuple, goal: tuple, goal_positions: dict = None, N: int = 3):
    if N % 2 == 0:
        raise ValueError("Nilsson's Sequence Score heuristic is only defined for odd N (e.g., 3x3, 5x5).")

    manhattan_distance, _ = h_manhattan(state, goal, goal_positions, N)

    # Nilsson ring order initialization: 0,1,2,5,8,7,6,3 (clockwise from top-left corner)
    ring_order = generate_ring_order(N=N)

    sequence_score = 0

    # Check the ring order for misplaced tiles (ignoring the blank tile)
    for i in range(len(ring_order)):
        curr_tile = state[ring_order[i]]

        # Ignore the blank tile when calculating sequence score
        if curr_tile == 0:
            continue

        # expected successor of this tile in goal state
        # In N-puzzle, successor is tile+1 except N*N-1
        expected_successor = 1 if curr_tile == N*N-1 else curr_tile + 1

        next_tile = state[ring_order[(i + 1) % len(ring_order)]]

        if next_tile != expected_successor:
            sequence_score += 2

    # center penalty
    center = N*N // 2
    if state[center] != 0:
        sequence_score += 1
    
    # The sequence score is multiplied by 3 to give it more weight compared to the Manhattan distance.
    # f(n) = g(n) + h(n) where h(n) = P(n) + 3 * S(n)
    fn = manhattan_distance + 3 * sequence_score
    return fn, sequence_score

In [14]:
start, goal = parse_astar_in(INPUT_FILE)

tracemalloc.start()
t0 = perf_counter()
path, N = astar_algorithm(start, goal, h_nilsson)

elapsed = perf_counter() - t0

current, peak = tracemalloc.get_traced_memory()
tracemalloc.stop()

print_path(path, N=N)
print(f"time={elapsed:.4f}s  current={current/1e6:.2f}MB  peak={peak/1e6:.2f}MB")

Expanding: g=0  h=60  f=60  P=60  S=13
Expanding: g=1  h=59  f=60  P=59  S=13
Expanding: g=1  h=59  f=60  P=59  S=13
Expanding: g=2  h=60  f=62  P=60  S=13
Expanding: g=2  h=60  f=62  P=60  S=13
Expanding: g=3  h=59  f=62  P=59  S=13
Expanding: g=1  h=64  f=65  P=64  S=14
Expanding: g=2  h=60  f=62  P=60  S=13
Expanding: g=2  h=60  f=62  P=60  S=13
Expanding: g=3  h=59  f=62  P=59  S=13
Expanding: g=3  h=59  f=62  P=59  S=13
Expanding: g=3  h=59  f=62  P=59  S=13
Expanding: g=4  h=60  f=64  P=60  S=13
Expanding: g=5  h=58  f=63  P=58  S=12
Expanding: g=6  h=54  f=60  P=54  S=11
Expanding: g=6  h=54  f=60  P=54  S=11
Expanding: g=7  h=53  f=60  P=53  S=11
Expanding: g=7  h=53  f=60  P=53  S=11
Expanding: g=4  h=60  f=64  P=60  S=13
Expanding: g=5  h=59  f=64  P=59  S=13
Expanding: g=5  h=59  f=64  P=59  S=13
Expanding: g=6  h=60  f=66  P=60  S=13
Expanding: g=7  h=59  f=66  P=59  S=13
Expanding: g=8  h=52  f=60  P=52  S=11
Expanding: g=9  h=51  f=60  P=51  S=11
Expanding: g=10  h=50  f=